# Exercise - Forecasting with Fundamentals

# 1. Carry Strategy for Dividend Yield

In this exercise, we consider the dividend-yield of individual stocks in order to invest in **high-carry** securities.

Note that we could consider the full analysis below with other metrics, including the PE ratio provided in the same data set.

#### Data

Use the data in `data/spx_data_weekly.xlsx`.
* `spx data` - time-series data for price, dividend-price ratio, and price-earnings ratio
* `sector data` - ETFs on sub-sectors
* `additional data` - `SPY`, `SHV`, and other benchmarks
* `rates data` - index levels for rates

Risk-free rate could be 
* `SHV`
*  `USGG3M Index` - annualized percent

In [ ]:
import pandas as pd

FILE_DATA = '../data/spx_data_weekly.xlsx'
SHEET_INFO = 'spx names'

info = pd.read_excel(FILE_DATA,sheet_name=SHEET_INFO)
info.set_index('ticker',inplace=True)
info.rename(columns={'security_name':'security name'},inplace=True)

display(info)

name        gics_sector_name       mkt cap
ticker                                                                  
A         Agilent Technologies Inc             Health Care  4.162353e+10
AAPL                     Apple Inc  Information Technology  4.025226e+12
ABBV                    AbbVie Inc             Health Care  4.106695e+11
ABNB                    Airbnb Inc  Consumer Discretionary  7.510938e+10
ABT            Abbott Laboratories             Health Care  2.270793e+11
...                            ...                     ...           ...
XYZ                      Block Inc              Financials  3.675158e+10
YUM                Yum! Brands Inc  Consumer Discretionary  4.137582e+10
ZBH     Zimmer Biomet Holdings Inc             Health Care  1.781850e+10
ZBRA       Zebra Technologies Corp  Information Technology  1.218683e+10
ZTS                     Zoetis Inc             Health Care  5.324455e+10

[503 rows x 3 columns]

In [ ]:
def load_ts(file_data,sheet_name):
    ts = pd.read_excel(file_data,sheet_name=sheet_name,
                    header=[0,1],                  
                    index_col=0)
                    
    ts.columns.names = ["ticker","field"]

    ts.rename(columns={
        'PX_LAST':'price',
        'EQY_DVD_YLD_IND':'dvd yld',
        'PE_RATIO':'pe ratio'
    }, level=1, inplace=True)

    return ts

In [ ]:
SHEET_TS = 'spx data'
spx = load_ts(FILE_DATA,SHEET_TS)
display(spx.tail().style.format('{:.2f}',na_rep='').format_index(lambda x: x.strftime('%Y-%m-%d')))

### 1.0. Data Processing

Filter the data to drop any ticker which does not have at least `5` years of continuous price data.

### 1.1. Data Processing

Report the highest and lowest dividend-yielding stocks...

* for any given date across the entire panel
* taking an average of the past year

Which stocks were they? Was it driven more by changes in D or P?

### 1.2. A Carry Strategy

For this strategy, use the `dvd yld` data.

Build a portfolio where at every time $t$, you set weights, $w_t$ that invest...
* long the highest ranking `20%` stocks.

For now, go equal weights of `0.01` in any stock for which you're long or short. 

#### Realized Returns
Start at the beginning of the sample.
* At time $t$, rank the stocks. 
* The selected stocks will earn $r_{t+1}$.

### 1.3. Long-Short

Re-do the strategy of the previous section, but this time go long and short...

At any given time $t$, set the vector $w_t$ as follows...
* long the highest-ranking `20%` of stocks.
* short the lowest-ranking `20%` of stocks.
* take no position in all other stocks.

### 1.4. Performance

Calculate the return of your portfolio over time. 

Report the following annualized stats
* mean
* volatility
* Sharpe 

Also calculate the tail-risk stats
* skewness
* VaR (5th quantile)
* CVaR (5th quantile)
* max drawdown

For both tables, compare to `SPY`, found in the `additional data` tab.

In [ ]:
SHEET_BENCH = 'additional data'
bench = load_ts(FILE_DATA,SHEET_BENCH)
display(bench[['SPY']].tail().style.format('{:.2f}',na_rep='').format_index('{:%Y-%m-%d}'))

***

# 2. Attribution

### 2.1. Market Exposure

For both the long-only (LO) and long-short (LS) strategies, estimate a linear factor decomposition (LFD) against `SPY`

Report the...
* alpha (annualized)
* beta
* r-squared

Also show the correlation matrix of the strategies.

How do the LO and LS strategies compare to `SPY`?

### 2.2. Sector Regression

Estimate a multivariate LFD for both LO and LS against all the sector ETFs.
* Note that `SHV` is not a sector ETF but rather a money-market fund. Exclude it.
* Exclude `SPY`.

Report the same stats as in `2.1.`

In [ ]:
SHEET_SECTOR_INFO = 'sector names'
info_sectors = pd.read_excel(FILE_DATA,sheet_name=SHEET_SECTOR_INFO).rename(columns={'Unnamed: 0':'ticker'}).set_index('ticker').drop(columns=['gics_sector_name'])
info_sectors['cur_mkt_cap'] = info_sectors['cur_mkt_cap'].astype(float) / 1e9
info_sectors.rename(columns={'cur_mkt_cap':'fund size ($ billions)'},inplace=True)
display(info_sectors.style.format({'fund size ($ billions)':'${:,.2f}'}))

In [ ]:
SHEET_SECTORS = 'sector data'
sectors = load_ts(FILE_DATA,SHEET_SECTORS)
display(sectors.tail().style.format('{:.1f}',na_rep='').format_index(lambda x: x.strftime('%Y-%m-%d')))

### 2.3. Sector Neutrality

Is your LO or LS implementation of the carry strategy neutral to sectors? To which sector does it have the largest exposure?

**Remember**

Unless regressors are standardized, comparing betas directly can be misleading. You might consider comparing $\beta_i\sigma_i$ when deciding which exposure is most substantial.

### 2.4. Magnificent Seven

Construct an equally-weighted portfolio of the following tickers. Call this `MAG`. Estimate a LFD on both `SPY` and `MAG`. Do this for both the LO and LS strategies.

Report the stats from `2.1`.

Comment on what you conclude from this regression.

In [ ]:
TICKS_MAG = ['AAPL','MSFT','GOOG','AMZN','NVDA','META','TSLA']
display(TICKS_MAG)

['AAPL', 'MSFT', 'GOOG', 'AMZN', 'NVDA', 'META', 'TSLA']

***

# 3. Dynamic hedged

It's one thing to ex-post evaluate whether the strategy had alpha beyond sector exposures. That raises the question as to whether we can caputre that when we're imperfectly hedging the sector exposure in real time.

At each date we:

1. Look back over a rolling 5-year window of weekly data.
2. Regress the portfolio return on the sector ETF returns.
3. Use the estimated betas as hedge ratios going forward one step.
4. Form a sector-hedged return by combining the strategy with
   an offsetting position in the sector ETFs.

We do this for both the long-only and long-short variants.

### 3.1.

Report the univariate stats of the hedged strategies.

### 3.2. 

Report sector LFD of the sector-hedged strategies.

***

# 4. Assessing the Forecast

Up to this point we did **not** build an explicit return forecast;
we jumped straight from a signal (dividend yield) to positions.

We could introduce the intermediate step of the return forecasts to try to understand whether the performance is driven by forecasting vs positioning. For illustration, consider the following forecasts:

- **+0.1%** for stocks we go long (top sorted)
- **−0.1%** for stocks we short (bottom sorted).

### 4.1.
- Treat those implied forecasts as a cross-sectional predictor of
  next-period returns.
- Compute an "out-of-sample" $R^2$ for the forecast vs realized
  returns.
- Compute the correlation between the forecast and realized returns.

### 4.2.

In section `3`, we considered a hedged strategies. Repeat `4.1` but this time interpreting our forecasts as pertaining to the hedged residuals of an LFD.

That is, build the forecasts identically, but compare them to the realized $\epsilon_t$ rather than the realized $r_t$. 

Use `SPY` as the single hedging factor. Be careful to estimate $\epsilon_t$ each period with data up to that point in time, rather than using the full sample.

### 4.3.

Repeat `4.2.` but considering all the sectors as the LFD.

***

# 5. No-Arbitrage via Cross-Asset Replication

If an asset can be replicated by other assets, an arbitrage-free model should assign consistent forecasts to the asset and its replication portfolio.

### 5.1. LASSO Replication and Forecast Consistency

For a selected asset, use LASSO to find a replication portfolio. Compare the dividend-yield-based forecast for the target asset vs its replication portfolio. 

### 5.2. Arbitrage

Do your forecasts imply arbitrage?

***

# 6. EXTRA - Improvements

### Allocation
Use a different allocation scheme. Above we used equal weightings for any stock that ranked above/below a certain threshold. Other allocations that overweight carry or value could be interesting.

### Signal
Point estimates of the signal may be noisy or misleading. Filter outlier values and take a rolling average of the signal.

### Sorting with Sector Neutrality
Rather than ranking the entire set, rank and allocate within each sector separately, ensuring sector neutrality.

### Momentum
Add a rule that you do not invest in the worst performing stocks over the past year, even if they rank well. And you do not short the best performing stocks over the past year, even if they rank poorly by our signal.